In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import folium
from folium import plugins

## Example data

In [2]:
df_population = pd.read_csv('data/Population Data.csv')
city_coords = df_population[['Lat','Lon']].values

In [3]:
city_coords[:3]

array([[  36.0122, -115.0375],
       [  42.9847,  -71.4439],
       [  40.6663,  -74.1935]])

### EasyMap

In [46]:
def easy_map(coords):
    """Make a marker for each (lat, long) pair. Plot on a map
    centered by the average position. """
    center = coords.mean(axis = 0)
    m = folium.Map(location = center, zoom_start=3.4)
    for i, coord in enumerate(coords):
        tooltip=f"{i}"
        folium.Marker(
            list(coord), tooltip=tooltip
        ).add_to(m)
    
    return m

In [47]:
easy_map_ex = easy_map(city_coords)
easy_map_ex

In [48]:
easy_map_ex.save('output/easy_map_example.html')

### Timestamped Temperature Map

#### Import data and do required data manipulation
We need to turn these two tables from the bp_weather challenge into the GeoJSON format, so we can use them in a TimestampedGeoJson map. 

In [72]:
## Import city-temp vs. time df
df_daily_temp_by_city = pd.read_csv('data/daily_temps_interpolated_2020.csv')

In [73]:
# Evaluate the inner tuples, so they're no longer strings
from ast import literal_eval
for i in range(3, len(df_daily_temp_by_city.columns)):
    df_daily_temp_by_city.iloc[:,i] = df_daily_temp_by_city.iloc[:,i].apply(lambda x: literal_eval(x))

#Convert to datetimes
df_daily_temp_by_city.datetime = pd.to_datetime(df_daily_temp_by_city.datetime)

In [74]:
df_daily_temp_by_city.head(3)

Unnamed: 0  Unnamed: 0.1   datetime  \
0           0             0 2020-01-01   
1           1             1 2020-01-02   
2           2             2 2020-01-03   

                                   Henderson, Nevada  \
0  (7.307898694836773, 3.961624631593768, 11.2416...   
1  (10.611569691467663, 4.47576454485819, 15.6706...   
2  (10.156613374292968, 5.058032012157768, 15.720...   

                           Manchester, New Hampshire  \
0  (3.425676850667078, 2.0745881854844614, 5.0657...   
1  (4.681301275945796, 1.0021818832820422, 8.3607...   
2  (8.465478440692047, 6.727593697797581, 9.94910...   

                               Elizabeth, New Jersey  \
0  (3.6312720471005804, 1.5740372809768266, 5.644...   
1  (5.215030927749299, 0.9340242792023131, 9.3722...   
2  (8.49439057073326, 7.187767798931417, 9.416814...   

                                  Newark, New Jersey  \
0  (3.6317505808217194, 1.591566348651684, 5.6392...   
1  (5.226733444971976, 0.9562654931513213, 9.3771...   
2  (8.49644572309581, 7.189971449262984, 9.415296...   

                                Paterson, New Jersey  \
0  (3.6382308906274137, 1.4947006982598825, 5.680...   
1  (5.16062428162862, 0.8232355270793476, 9.36245...   
2  (8.4933051284179, 7.18372421004967, 9.43340409...   

                             Jersey City, New Jersey  \
0  (3.6302175518585647, 1.6646754098954766, 5.613...   
1  (5.276098824416904, 1.0529433786125837, 9.3928...   
2  (8.501839704245292, 7.196868876563811, 9.40520...   

                             Albuquerque, New Mexico  ...  \
0  (5.864600554023262, 1.195546534960726, 10.9514...  ...   
1  (5.591363938753055, 1.8490911858357755, 10.977...  ...   
2  (5.850677768354682, 0.12026197423868765, 12.15...  ...   

                                    Miramar, Florida  \
0  (9.305988852137737, 4.754780458801245, 14.0456...   
1  (12.51702957922572, 8.875838593045273, 15.4064...   
2  (13.940201237461512, 10.978783170511417, 17.27...   

                                    Hialeah, Florida  \
0  (9.315918976161312, 4.7649389721071955, 14.052...   
1  (12.537561556199673, 8.887013733723247, 15.431...   
2  (13.942949277524706, 10.98614123424478, 17.280...   

                              Coral Springs, Florida  \
0  (9.241267304578683, 4.690100872064729, 14.0015...   
1  (12.390334154083675, 8.779238532026064, 15.276...   
2  (13.904917133059888, 10.921582582130217, 17.20...   

                              Miami Gardens, Florida  \
0  (9.291180066239152, 4.740361706146202, 14.0355...   
1  (12.48981189706693, 8.847828965176635, 15.3846...   
2  (13.927809645388047, 10.963397791490854, 17.25...   

                                      Miami, Florida  \
0  (9.310965105012196, 4.760428658659115, 14.0489...   
1  (12.529914269577754, 8.87278279432198, 15.4307...   
2  (13.93525018256813, 10.979103759691974, 17.273...   

                                  Hollywood, Florida  \
0  (9.26171873009238, 4.711150123241109, 14.01544...   
1  (12.433213831273521, 8.80027525135865, 15.3302...   
2  (13.909130116099389, 10.935967085517724, 17.22...   

                            Fort Lauderdale, Florida  \
0  (9.239340208149134, 4.688771556410303, 14.0002...   
1  (12.389339081014894, 8.767100183447148, 15.284...   
2  (13.897095264510007, 10.916276946171184, 17.20...   

                              Pompano Beach, Florida  \
0  (9.219179192681601, 4.66859693210946, 13.98649...   
1  (12.349748745298813, 8.737423130883048, 15.243...   
2  (13.886406972411969, 10.898619859304763, 17.18...   

                            West Palm Beach, Florida  \
0  (9.12692280765972, 4.575973765967915, 13.92373...   
1  (12.167166483752915, 8.606349502658384, 15.049...   
2  (13.840954060128599, 10.819660331773061, 17.09...   

                                         daily_temps  
0  (7.349019044192506, 2.978441322887563, 11.8712...  
1  (9.243244739257591, 5.513192221925491, 13.4096...  
2  (10.044711656832355, 6.551199372524534, 14.304

In [76]:
#df_pop = pd.read_csv('data/Population Data.csv')

In [79]:
def citystate_to_latlong(df_pop, continental_only = False):
    """Builds a map between 'City, State' and (Lon, Lat). """
    cs_latlong = {}
    for row in df_pop[['City', 'State', 'Lon', 'Lat']].values:
        if row[1] in {"Alaska", "Hawaii"} and continental_only == True:
            continue
        cs_latlong[f"{row[0]}, {row[1]}"] = (row[2], row[3])
        
    return cs_latlong

def citystate_to_temps(df_daily_temp_by_city, citystate_latlong):
    """Build a map between 'City, State' and temps [T_0, T_1, ..., T_N]"""
    cs_temps = {}
    for k, v in citystate_latlong.items():
        cs_temps[k] = [t[0] for t in df_daily_temp_by_city[k].values]
    return cs_temps

In [80]:
class TemperatureTimeSeries:
    """Class to simplify working with city locations and temperature timeseries."""
    def __init__(self, city_to_coord, city_daily_temps):
        self.city_to_coord = city_to_coord
        self.city_daily_temps = city_daily_temps
        self.coords =[[c[1], c[0]] for c in list(city_to_coord.values())]
        self.temp_vals = list(city_daily_temps.values())
        
        self.times = list(range(0, len(self.temp_vals[0])))
        self.normalization_vals = (-100, 100)
        
        
    def transform_for_heatmap(self, normalized = None):
        """Desired: 
        [ [[lat_a, long_a, T_a0], ... [lat_z, long_z, T_z0]],
            ...
            [[lat_a, long_a, T_aN], ... [lat_z, long_z, T_zN]] ] """
        spatial_temps_over_time = []

        for t in self.times:
            pos_with_temps = []
            for i, (lat, long) in enumerate(self.coords):
                if normalized is None:
                    pos_with_temps.append([lat, long, self.temp_vals[i][t]])
                else:
                    pos_with_temps.append([lat, long, self.normalize(temp_vals[i][t])])
                    
                    
            spatial_temps_over_time.append(pos_with_temps)
            
        return spatial_temps_over_time
    
    def normalize(self, x):
        normed = (x - self.normalization_vals[0])/ (self.normalization_vals[1] - self.normalization_vals[0])
        return normed

In [81]:
cs_latlong =  citystate_to_latlong(df_population, continental_only=True)
cs_temps = citystate_to_temps(df_daily_temp_by_city, cs_latlong)
temp_tseries = TemperatureTimeSeries(cs_latlong, cs_temps)

In [82]:
# Make a big 3D array of size (num_datetimes x num_cities x 3), inner elements are
# (lat, long, Temperature) for a given datetime.
spatial_temps_by_time = temp_tseries.transform_for_heatmap()
times = df_daily_temp_by_city.datetime.values

In [85]:
spatial_temps_by_time[10][:5]

[[36.0122, -115.0375, 6.362102531105577],
 [42.9847, -71.4439, 14.542825361466821],
 [40.6663, -74.1935, 13.914048763368433],
 [40.7242, -74.1726, 13.907700321054309],
 [40.9147, -74.1628, 13.94568275913876]]

In [86]:
# The 10th element of spatial_temps_by_time corresponds to datetime:
times[10]

numpy.datetime64('2020-01-11T00:00:00.000000000')

In [87]:
def make_heatmap(data):
    """Make heatmap across time, which takes in an array of arrays of [lat,long,value],
    using HeatMapWithTime. NOTE: Weights must be small numbers (between 0 and 2?)."""
    print(f"Number of times = {len(data)}.")
    print(f"Number of positions = {len(data[0])}.")
    # Max temperature = 50
    
    coords = np.array([d[:2] for d in data[0]])
    
    center = coords.mean(axis = 0)
    m = folium.Map(location = center, zoom_start=3.4)
    # Make heatmap...
    hm = plugins.HeatMapWithTime(data, auto_play=True,max_opacity=0.8, max_speed=1000, radius = 5)

    hm.add_to(m)
    return m

This heatmap works, but I'm actually looking for a chloropleth, since heatmaps will add up the temperatures (so dense regions will always look "hot"). Another solution is to just plot points in time on a map, with color determined by temperature. 

Can do this using folium's TimestampedGeoJson.

In [88]:
# This sets the minimum and maximum temperatures, as well as the bin-width for visualization
temp_bins = list(range(-20, 45, 1))
color_scale = sns.color_palette("coolwarm", len(temp_bins)).as_hex()

In [89]:
print(len(temp_bins), len(color_scale))

65 65


In [90]:
def color_coding(poll, bin_edges):    
    idx = np.digitize(poll, bin_edges, right=True)
    try:
        color = color_scale[idx]
    except:
        color = color_scale[-1]

    return color

In [91]:
color_coding(50, temp_bins)

'#b8122a'

In [100]:
# Use TimestampedGeoJson(data)
# Inspired by: https://towardsdatascience.com/visualizing-air-pollution-with-folium-maps-4ce1a1880677
def generate_geojson_features(spatial_temps_by_time, times, temp_edges):
    """
    This transforms this data, along with timestamps into a GeoJSON
    format (list of feature dictionaries), so it can be passed to 
    folium.plugins.TimestampedGeoJson().
    """
    print('> Creating GeoJSON features...')
    features = []
    for t_i, spatial_temps in enumerate(spatial_temps_by_time):
        # This is all [lat,long,T] at t=t_i
        for (lat, long, T) in spatial_temps:
            time = times[t_i]
            # Temp to color
            color =  color_coding(T, temp_edges)
            feature = {
                'type': 'Feature',
                'geometry': {
                    'type':'Point', 
                    'coordinates':[long, lat]
                },
                'properties': {
                    'time': str(time),
                    'style': {'color' : color},
                    'icon': 'circle',
                    'iconstyle':{
                        'fillColor': color,
                        'fillOpacity': 0.8,
                        'stroke': 'true',
                        'radius': 7
                    }
                }
            }
            features.append(feature)
        
    return features

2020 Temperature map data

In [101]:
# Use the times from the dataframe, build 1 year (365 days) worth,
# 6 years worth is 670k points and won't render.
geo_features =  generate_geojson_features(spatial_temps_by_time[::10], times[::10], temp_bins)

> Creating GeoJSON features...


In [102]:
geo_features[0], geo_features[-1]

({'type': 'Feature',
  'geometry': {'type': 'Point', 'coordinates': [-115.0375, 36.0122]},
  'properties': {'time': '2020-01-01T00:00:00.000000000',
   'style': {'color': '#ccd9ed'},
   'icon': 'circle',
   'iconstyle': {'fillColor': '#ccd9ed',
    'fillOpacity': 0.8,
    'stroke': 'true',
    'radius': 7}}},
 {'type': 'Feature',
  'geometry': {'type': 'Point', 'coordinates': [-80.1266, 26.7483]},
  'properties': {'time': '2020-12-26T00:00:00.000000000',
   'style': {'color': '#afcafc'},
   'icon': 'circle',
   'iconstyle': {'fillColor': '#afcafc',
    'fillOpacity': 0.8,
    'stroke': 'true',
    'radius': 7}}})

In [103]:
# Make GeoJSON vs Time map
from folium import plugins
def map_timestamped_GeoJSON(features, transition_time = 200, max_speed=10000):
    """Make GeoJSON map, from a list of GeoJson features."""
    print(f"Total number of points: {len(features)}")
    
    center = [39.5, -98.35] # Center of continental US
    temp_timemap = folium.Map(location=center, zoom_start=4, prefer_canvas=True)

    plugins.TimestampedGeoJson(
        {'type': 'FeatureCollection', 'features': features}, 
        max_speed=max_speed, transition_time=transition_time).add_to(temp_timemap)
    
    return temp_timemap

In [104]:
temp_timemap = map_timestamped_GeoJSON(geo_features)

Total number of points: 10471


In [105]:
temp_timemap

In [106]:
temp_timemap.save('output/temperature_vs_time_2020.html')

In [107]:
# Color map varies from -20 to 40 degrees.
sns.color_palette("coolwarm", 17)

[(0.29471843211764703, 0.39354192974117647, 0.8343841671215686),
 (0.3634607953411765, 0.4847836818509804, 0.9010188868941177),
 (0.4358148063058824, 0.5707073031529412, 0.951717381282353),
 (0.5108243242509803, 0.6493966148235294, 0.9850787763764707),
 (0.5923558594980393, 0.7227920292549019, 0.9994338748235294),
 (0.6672529243333334, 0.7791764569999999, 0.992959213),
 (0.7388259949411764, 0.8225716218235294, 0.9682610638235294),
 (0.8049647588235295, 0.8516661605568627, 0.9261650744313725),
 (0.8674276350862745, 0.864376599772549, 0.8626024620196079),
 (0.9193759889058823, 0.8312727235294118, 0.7828736304470588),
 (0.9527607176705882, 0.7829647976, 0.6986457713058823),
 (0.968203399, 0.7208441, 0.6122929913333334),
 (0.9660167198392157, 0.6461297415882352, 0.5258903482588235),
 (0.9440545734235294, 0.5531534787490197, 0.4355484903137255),
 (0.9057834780117647, 0.4551856921647059, 0.35533588384705883),
 (0.8523781350078431, 0.34649194649411763, 0.2803464686980392),
 (0.7851533046784314, 0.2208510887215686, 0.21167287700784312)]